<a href="https://colab.research.google.com/github/buvnswrn/CNTG-Project/blob/main/Final_Training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# DAML-ST5 Training

The training procedure of DAML-ST5

Deployment URL: https://huggingface.co/buvnswrn/daml-t5-training


## Check Hardware Details

Verifying which GPU is allocated

In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Mon Apr 11 17:21:41 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   37C    P0    26W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

Verifying the runtime type (RAM)

In [ ]:
from psutil import virtual_memory
ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))

if ram_gb < 20:
  print('Not using a high-RAM runtime')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 27.3 gigabytes of available RAM

You are using a high-RAM runtime!


## Check Pre-requisites

In [ ]:
!pip install datasets transformers[sentencepiece]
!pip install accelerate
# To run the training on TPU, you will need to uncomment the followin line:
# !pip install cloud-tpu-client==0.10 torch==1.9.0 https://storage.googleapis.com/tpu-pytorch/wheels/torch_xla-1.9-cp37-cp37m-linux_x86_64.whl
!apt install git-lfs

     |████████████████████████████████| 325 kB 7.1 MB/s 
     |████████████████████████████████| 4.0 MB 62.3 MB/s 
     |████████████████████████████████| 212 kB 80.0 MB/s 
     |████████████████████████████████| 77 kB 8.1 MB/s 
     |████████████████████████████████| 136 kB 87.8 MB/s 
     |████████████████████████████████| 1.1 MB 62.0 MB/s 
     |████████████████████████████████| 127 kB 81.9 MB/s 
     |████████████████████████████████| 271 kB 70.3 MB/s 
     |████████████████████████████████| 144 kB 75.2 MB/s 
     |████████████████████████████████| 94 kB 4.2 MB/s 
     |████████████████████████████████| 6.5 MB 49.2 MB/s 
     |████████████████████████████████| 895 kB 62.9 MB/s 
     |████████████████████████████████| 596 kB 57.0 MB/s 
     |████████████████████████████████| 1.2 MB 68.0 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempting uninstall: pyyaml
   

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
PATH = "/content/drive/MyDrive/CNTG/"

## Dataset

### Load the IMDB Dataset

In [ ]:
from datasets import load_dataset, load_metric

raw_datasets = load_dataset("imdb")

Generating train split:   0%|          | 0/25000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/25000 [00:00<?, ? examples/s]

Generating unsupervised split:   0%|          | 0/50000 [00:00<?, ? examples/s]

Dataset imdb downloaded and prepared to /root/.cache/huggingface/datasets/imdb/plain_text/1.0.0/2fdd8b9bcadd6e7055e742a706876ba43f19faee861df134affd7a3f60fc38a1. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
split_datasets = raw_datasets["train"].train_test_split(train_size=0.5, seed=20)

In [ ]:
split_datasets["validation"] = split_datasets.pop("test").train_test_split(train_size=0.5, seed=20)["test"]

In [ ]:
split_datasets

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 12500
    })
    validation: Dataset({
        features: ['text', 'label'],
        num_rows: 6250
    })
})

### Load the Amazon Dataset

Just run this on second iteration of training

In [ ]:
from datasets import load_dataset, load_metric

# raw_datasets = load_dataset("imdb")
# raw_datasets = load_dataset("yelp_polarity")
raw_datasets = load_dataset("amazon_polarity")

Generating train split:   0%|          | 0/3600000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/400000 [00:00<?, ? examples/s]

Dataset amazon_polarity downloaded and prepared to /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/56923eeb72030cb6c4ea30c8a4e1162c26b25973475ac1f44340f0ec0f2936f4. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
split_datasets = raw_datasets["train"].train_test_split(train_size=0.005, seed=20)

Loading cached split indices for dataset at /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/56923eeb72030cb6c4ea30c8a4e1162c26b25973475ac1f44340f0ec0f2936f4/cache-b87e3ed5e03d6911.arrow and /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/56923eeb72030cb6c4ea30c8a4e1162c26b25973475ac1f44340f0ec0f2936f4/cache-c233ff351379ccba.arrow


In [ ]:
split_datasets["validation"] = split_datasets.pop("test").train_test_split(train_size=0.005, seed=20)["train"]

Loading cached split indices for dataset at /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/56923eeb72030cb6c4ea30c8a4e1162c26b25973475ac1f44340f0ec0f2936f4/cache-9a088dc88b9adda4.arrow and /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/56923eeb72030cb6c4ea30c8a4e1162c26b25973475ac1f44340f0ec0f2936f4/cache-0ff4bf498315026b.arrow


In [ ]:
split_datasets

DatasetDict({
    train: Dataset({
        features: ['label', 'title', 'content'],
        num_rows: 18000
    })
    validation: Dataset({
        features: ['label', 'title', 'content'],
        num_rows: 17910
    })
})

### Load the yelp Dataset [For Evaluation]

In [ ]:
from datasets import load_dataset, load_metric

raw_datasets = load_dataset("yelp_polarity")

Generating train split:   0%|          | 0/560000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/38000 [00:00<?, ? examples/s]

Dataset yelp_polarity downloaded and prepared to /root/.cache/huggingface/datasets/yelp_polarity/plain_text/1.0.0/a770787b2526bdcbfc29ac2d9beb8e820fbc15a03afd3ebc4fb9d8529de57544. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
split_datasets = raw_datasets["train"].train_test_split(train_size=0.005, seed=20)

In [ ]:
split_datasets["validation"] = split_datasets.pop("test").train_test_split(train_size=0.005, seed=20)["train"]

In [ ]:
split_datasets

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 2800
    })
    validation: Dataset({
        features: ['text', 'label'],
        num_rows: 2786
    })
})

### Test the dataset

In [ ]:
raw_datasets

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 560000
    })
    test: Dataset({
        features: ['text', 'label'],
        num_rows: 38000
    })
})

In [ ]:
split_datasets

DatasetDict({
    train: Dataset({
        features: ['text', 'label'],
        num_rows: 2800
    })
    validation: Dataset({
        features: ['text', 'label'],
        num_rows: 2786
    })
})

In [ ]:
# split_datasets["train"][1]["content"] # Uncomment this when amazon dataset is used 
split_datasets["train"][1]["text"]

'I\'ve attempted to go to this place before, not realizing it was either shut down or didn\'t exist? (following the signs to grand cafe led nowhere, which is a pain when you\'re wandering through a casino very hungry!) \\nFinally, it was open and being in the mood for some diner-fare food, we decided to give it a try. By the looks of this place, it was well worth the wait. The inside is gorgeous and makes you feel like you\'re about to enjoy some 5 star dining.... \\n\\nToo bad the food and service were awful. We were seated right away. It was fairly late on a Sunday night so we didn\'t have many tables to compete with. We didn\'t get the usual \\""water while you wait\\"" drop off and actually ended up not receiving our beverages until we got our entrees! I did order the french onion soup... its kind of rare to find it on a menu, so I wanted to try it. Mine was lukewarm, my husband\'s was even colder than that. I nearly choked on the dried out, cheap grated cheese that was piled on to

In [ ]:
split_datasets["train"][172]["text"]

'Stopped in to grab breakfast in this place since it was in the Mandalay where we were staying and it was pretty good. It sits in the back of the casino and it has a ful menu including take out sandwiches which looked delicious and breakfast items. \\n\\nWe ate some eggs and toast etc, but the best was the crumbled tater tots mixed with red peppers, best I have tasted. It gets pretty crowded and you may end up waiting but it was worth it. Prices were right and service was fast and friendly! Place is decorated like a kitchen and it was pretty cool inside. Not sure what the dinner menu looks like but it might be good!'

## Reconstruction Model

**Load the T5 Base Model translation pipeline**

**Use the pretrained tokenizer**

In [ ]:
from transformers import AutoTokenizer

# Uncomment the below line based on what data you're running

# tokenizer_checkpoint = "buvnswrn/t5-base-imdb-tokenizer-512"
tokenizer_checkpoint = "buvnswrn/t5-base-yelp-tokenizer"
# tokenizer_checkpoint = "buvnswrn/t5-base-amazon-tokenizer"
rec_tokenizer = AutoTokenizer.from_pretrained(tokenizer_checkpoint, return_tensors="tf")

Downloading:   0%|          | 0.00/1.91k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.88M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.74k [00:00<?, ?B/s]

#### Test the tokenizer

In [ ]:
en_sentence = split_datasets["train"][1]["text"] # comment this if amazon is used
# en_sentence = split_datasets["train"][1]["content"] # Uncomment if amazon is used
fr_sentence = split_datasets["train"][1]["text"] # comment this line if amazon is used
# fr_sentence = split_datasets["train"][1]["content"] # 

inputs = rec_tokenizer(en_sentence)
with rec_tokenizer.as_target_tokenizer():
    targets = rec_tokenizer(fr_sentence)

In [ ]:
wrong_targets = rec_tokenizer(fr_sentence)
print(rec_tokenizer.convert_ids_to_tokens(wrong_targets["input_ids"]))
print(rec_tokenizer.convert_ids_to_tokens(targets["input_ids"]))

["▁I've", '▁attempted', '▁to', '▁go', '▁to', '▁this', '▁place', '▁before,', '▁not', '▁realizing', '▁it', '▁was', '▁either', '▁shut', '▁down', '▁or', "▁didn't", '▁exist', '?', '▁(', 'follow', 'ing', '▁the', '▁signs', '▁to', '▁grand', '▁cafe', '▁led', '▁nowhere', ',', '▁which', '▁is', '▁a', '▁pain', '▁when', "▁you're", '▁wandering', '▁through', '▁a', '▁casino', '▁very', '▁hungry', '!)', '▁', '\\nFinally', ',', '▁it', '▁was', '▁open', '▁and', '▁being', '▁in', '▁the', '▁mood', '▁for', '▁some', '▁diner', '-', 'fare', '▁food,', '▁we', '▁decided', '▁to', '▁give', '▁it', '▁a', '▁try.', '▁By', '▁the', '▁looks', '▁of', '▁this', '▁place,', '▁it', '▁was', '▁well', '▁worth', '▁the', '▁wait.', '▁The', '▁inside', '▁is', '▁gorgeous', '▁and', '▁makes', '▁you', '▁feel', '▁like', "▁you're", '▁about', '▁to', '▁enjoy', '▁some', '▁5', '▁star', '▁dining', '....', '▁\\n\\nTo', 'o', '▁bad', '▁the', '▁food', '▁and', '▁service', '▁were', '▁awful.', '▁We', '▁were', '▁seated', '▁right', '▁away.', '▁It', '▁was', '▁

### Preprocessing Function

In [ ]:
max_input_length = 128
max_target_length = 128


def preprocess_function(examples):
    inputs = [ex for ex in examples["text"]]
    # inputs = [ex for ex in examples["content"]]
    targets = [ex for ex in examples["text"]]
    # targets = [ex for ex in examples["content"]]
    model_inputs = rec_tokenizer(inputs, max_length=max_input_length, truncation=True)

    # Set up the tokenizer for targets
    with rec_tokenizer.as_target_tokenizer():
        labels = rec_tokenizer(targets, max_length=max_target_length, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    # model_inputs["prefix"] = prefix
    return model_inputs

### Tokenize the dataset

In [ ]:
tokenized_datasets = split_datasets.map(
    preprocess_function,
    batched=True,
    remove_columns=['text'] # comment for amazon dataset
    # remove_columns=['content','title'] #uncomment for amazon dataset
)

  0%|          | 0/3 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

In [ ]:
tokenized_datasets.set_format('torch',columns=['input_ids','attention_mask', 'labels','label'])

### Don't run this

In [ ]:
rec_tokenized_datasets = tokenized_datasets.map(
    remove_columns=['label']
)

  0%|          | 0/12500 [00:00<?, ?ex/s]

TypeError: ignored

In [ ]:
rec_tokenized_datasets["train"].column_names

In [ ]:
type(tokenized_datasets["train"][0])

In [ ]:
tokenized_datasets["train"][0]

### Fetch the model from Hugginface Hub

In [ ]:
from transformers import AutoModelWithLMHead
model_checkpoint = "buvnswrn/daml-t5-pretrain"
# model_checkpoint = "buvnswrn/daml-t5-training"
model = AutoModelWithLMHead.from_pretrained(model_checkpoint)

/usr/local/lib/python3.7/dist-packages/transformers/models/auto/modeling_auto.py:911: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  FutureWarning,


Downloading:   0%|          | 0.00/1.35k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/850M [00:00<?, ?B/s]

### Form Batch using Datacollator

In [ ]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(rec_tokenizer, model=model)

#### Test DataCollator [No need to run this]

In [ ]:
len(rec_tokenized_datasets.keys())

In [ ]:
len(tokenized_datasets["train"]["label"])

In [ ]:
len(rec_tokenized_datasets["train"]["labels"])

In [ ]:
tokenized_datasets["train"][0]["input_ids"].shape

In [ ]:
batch = custom_data_collator([tokenized_datasets["train"][i] for i in range(1, 3)])
# batch.keys()

In [ ]:
rec_tokenized_datasets["train"][1]

In [ ]:
batch

In [ ]:
batch

In [ ]:
batch["labels"]

In [ ]:
batch["decoder_input_ids"]

In [ ]:
for i in range(1, 3):
    print(tokenized_datasets["train"][i]["labels"])

## Discriminator

Using the discriminator that uses input ids instead of embedding bag

### Prerequisites

In [ ]:
import torch

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Model Definition

In [ ]:
from torch import nn
import torch.nn.functional as F
import torch

class StyleClassifier(nn.Module):

    def __init__(self, input_dim, hidden_dim, num_class):
        super(StyleClassifier, self).__init__()
        self.fc = nn.Linear(input_dim, hidden_dim)
        self.fc1 = nn.Linear(hidden_dim, hidden_dim)
        self.fc2 = nn.Linear(hidden_dim, hidden_dim)
        self.fc3 = nn.Linear(hidden_dim, num_class)
        self.softmax = torch.nn.Softmax()
        self.init_weights()

    def init_weights(self):
        initrange = 0.5
        self.fc.weight.data.uniform_(-initrange, initrange)
        self.fc1.weight.data.uniform_(-initrange, initrange)
        self.fc2.weight.data.uniform_(-initrange, initrange)
        self.fc3.weight.data.uniform_(-initrange, initrange)
        self.fc.bias.data.zero_()
        self.fc1.bias.data.zero_()
        self.fc2.bias.data.zero_()
        self.fc3.bias.data.zero_()

    def forward(self, text):
        hidden_1 = F.sigmoid(self.fc(text))
        hidden_2 = F.sigmoid(self.fc1(hidden_1))
        hidden_3 = F.sigmoid(self.fc2(hidden_2))
        output = F.sigmoid(self.fc3(hidden_3))
        return self.softmax(output)

### Model Initialization

In [ ]:
discriminator = StyleClassifier(max_input_length,512,2)

In [ ]:
discriminator.load_state_dict(torch.load(PATH+"disciminator-without-embeddingbag1.pt"))

<All keys matched successfully>

In [ ]:
discriminator.to(device)

StyleClassifier(
  (fc): Linear(in_features=128, out_features=512, bias=True)
  (fc1): Linear(in_features=512, out_features=512, bias=True)
  (fc2): Linear(in_features=512, out_features=512, bias=True)
  (fc3): Linear(in_features=512, out_features=2, bias=True)
  (softmax): Softmax(dim=None)
)

### Hyperparameters

In [ ]:
DISC_EPOCHS = 50
DISC_LR = 1e-5
BATCH_SIZE = 64

In [ ]:
from transformers import AdamW

# optimizer = AdamW(discriminator.parameters(), lr=DISC_LR)
optimizer = torch.optim.Adam(discriminator.parameters(), lr=DISC_LR)
criterion = torch.nn.CrossEntropyLoss()

### Dataloader

In [ ]:
from torch.utils.data import DataLoader

tokenized_datasets.set_format("torch")
train_dataloader = DataLoader(
    tokenized_datasets["train"],
    shuffle=True,
    collate_fn=data_collator,
    batch_size=BATCH_SIZE,
)
eval_dataloader = DataLoader(
    tokenized_datasets["validation"], collate_fn=data_collator, batch_size=BATCH_SIZE
)

In [ ]:
unseen_dataloader = train_dataloader # Uncomment for evaluation

### Train Function 

In [ ]:
import time

def trainDiscriminator(dataloader):
  discriminator.train()
  total_acc, total_count = 0, 0
  log_interval = 500
  start_time = time.time()
  for idx, data in enumerate(dataloader):
    input = data["input_ids"].type(torch.FloatTensor).to(device)
    label = data["label"].to(device)
    predicted_label = discriminator(input)
    predicted_label.type(torch.LongTensor)
    loss = criterion(predicted_label, label)
    loss.backward()
    torch.nn.utils.clip_grad_norm_(discriminator.parameters(),0.1)
    optimizer.step()
    total_acc += (predicted_label.argmax(1) == label).sum().item()
    total_count += label.size(0)
    if idx % log_interval == 0 and idx > 0:
        elapsed = time.time() - start_time
        print('| epoch {:3d} | {:5d}/{:5d} batches '
              '| accuracy {:8.3f}'.format(epoch, idx, len(dataloader),
                                          total_acc/total_count))
        total_acc, total_count = 0, 0
        start_time = time.time()

In [ ]:
def evaluateDiscriminator(dataloader):
  discriminator.eval()
  total_acc, total_count = 0, 0
  with torch.no_grad():
    for idx, data in enumerate(dataloader):
      predicted_label = discriminator(data["input_ids"].type(torch.FloatTensor).to(device))
      label = data["label"].to(device)
      loss = criterion(predicted_label, label)
      total_acc += (predicted_label.argmax(1) == label).sum().item()
      total_count += label.size(0)
  return total_acc/total_count

### Training

In [ ]:
total_accu = None
for epoch in range(1,DISC_EPOCHS+1):
  epoch_start_time = time.time()
  trainDiscriminator(train_dataloader)
  accu_val = evaluateDiscriminator(eval_dataloader)
  print('-' * 59)
  print('| end of epoch {:3d} | time: {:5.2f}s | '
        'valid accuracy {:8.3f} '.format(epoch,
                                          time.time() - epoch_start_time,
                                          accu_val))
  print('-' * 59)

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:32: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


-----------------------------------------------------------
| end of epoch   1 | time:  9.64s | valid accuracy    0.504 
-----------------------------------------------------------
-----------------------------------------------------------
| end of epoch   2 | time:  9.54s | valid accuracy    0.502 
-----------------------------------------------------------
-----------------------------------------------------------
| end of epoch   3 | time:  9.80s | valid accuracy    0.502 
-----------------------------------------------------------
-----------------------------------------------------------
| end of epoch   4 | time: 10.56s | valid accuracy    0.503 
-----------------------------------------------------------
-----------------------------------------------------------
| end of epoch   5 | time: 10.38s | valid accuracy    0.502 
-----------------------------------------------------------
-----------------------------------------------------------
| end of epoch   6 | time: 10.05s |

In [ ]:
torch.save(discriminator.state_dict(),PATH+"disciminator-without-embeddingbag1.pt")

## Custom Training Loop (Not using builtin method to train)

Deployment URL: https://huggingface.co/buvnswrn/daml-t5-training

In [ ]:
model_checkpoint = "buvnswrn/daml-t5-training" # comment when run first time

In [ ]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

reconstructor = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint)

In [ ]:
from transformers import AdamW

rec_optimizer = AdamW(reconstructor.parameters(), lr=2e-5)

/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:309: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


In [ ]:
from accelerate import Accelerator

rec_accelerator = Accelerator()
reconstructor, rec_optimizer, train_dataloader, eval_dataloader,discriminator = rec_accelerator.prepare(
    reconstructor, rec_optimizer, train_dataloader, eval_dataloader, discriminator
)

In [ ]:
from transformers import get_scheduler

num_train_epochs = 3
num_update_steps_per_epoch = len(train_dataloader)
num_training_steps = num_train_epochs * num_update_steps_per_epoch

lr_scheduler = get_scheduler(
    "linear",
    optimizer=optimizer,
    num_warmup_steps=0,
    num_training_steps=num_training_steps,
)

### Logging to Huggingface

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store


In [ ]:
!git config --global user.email "bhuvan.nav@gmail.com"
!git config --global user.name "buvnswrn"

In [ ]:
from huggingface_hub import Repository, get_full_repo_name

model_name = "daml-t5"
repo_name = get_full_repo_name(model_name)
repo_name

'buvnswrn/daml-t5'

### Don't run this

In [ ]:
output_dir = "daml-t5-training"
repo = Repository(output_dir, clone_from=repo_name)

KeyboardInterrupt: ignored

### Post-Process Function

In [ ]:
import numpy as np
def postprocess(predictions, labels):
    predictions = predictions.cpu().numpy()
    labels = labels.cpu().numpy()

    decoded_preds = rec_tokenizer.batch_decode(predictions, skip_special_tokens=True)

    # Replace -100 in the labels as we can't decode them.
    labels = np.where(labels != -100, labels, rec_tokenizer.pad_token_id)
    decoded_labels = rec_tokenizer.batch_decode(labels, skip_special_tokens=True)

    # Some simple post-processing
    decoded_preds = [pred.strip() for pred in decoded_preds]
    decoded_labels = [[label.strip()] for label in decoded_labels]
    return decoded_preds, decoded_labels

### Train DAML

#### Hyperparameters

In [ ]:
num_epochs = 3
# inner_learning_rate
alpha = 0.0001
# outer_learning_rate
beta = 0.001

LR = 1e-5
BATCH_SIZE = 64

#### Adaptation Steps

In [ ]:
from tqdm.auto import tqdm
def run_innerloop(data,training_progress_bar):
    training_progress_bar.reset()
    for i in range(0,len(data["input_ids"])):
      input = data["input_ids"][i].unsqueeze(0).to(device)
      label = data["label"][i].unsqueeze(0).to(device)
      reconstructed_sentence = reconstructor(input_ids=input, labels=data["labels"][i].unsqueeze(0).to(device))
      input = input.type(torch.FloatTensor).to(device)
      predicted_label = discriminator(input)
      predicted_label.type(torch.LongTensor)
      style_loss = criterion(predicted_label, label)
      for name, param in reconstructor.state_dict().items():
        if not "weight" in name:
          continue
        param.copy_(param - alpha * float(reconstructed_sentence.loss))
        param.copy_(param - alpha * float(style_loss))
      training_progress_bar.update(1)

In [ ]:
def save_model_to_hub(iter_no):
  reconstructor.save_pretrained("buvnswrn/daml-t5-training", commit_message=f"Updated on iteration{iter_no}")
  reconstructor.push_to_hub("daml-t5-training",commit_message=f"Updated on iteration{iter_no}")

In [ ]:
# rec_tokenizer.push_to_hub("daml-t5-training") # uncomment for first time

In [ ]:
len(eval_dataloader)
len(train_dataloader)

14063

In [ ]:
def start_training(count=0):
  reconstructor.train()
  discriminator.train()
  val_losses_batch_wise = {}
  val_batch_count = 0
  total_training_progress_bar = tqdm(range(len(eval_dataloader)),desc="Total Training")
  inner_training_progress_bar = tqdm(range(len(train_dataloader)),desc="Inner Loop training (No.of.Batches)")
  innerloop_training_progress_bar = tqdm(range(BATCH_SIZE),desc="Inner Loop training (No.of.examples in current batch)")
  val_progress_bar = tqdm(range(BATCH_SIZE),desc="Validation Examples in current batch")
  for v_idx, batch in enumerate(eval_dataloader):
    val_batch_count +=1
    inner_training_progress_bar.reset()
    if val_batch_count > count:
      for idx, data in enumerate(train_dataloader):
        torch.cuda.empty_cache()
        run_innerloop(data,innerloop_training_progress_bar)
        torch.cuda.empty_cache()
        val_losses = []
        val_progress_bar.reset()
        for j in range(0,len(batch["input_ids"])): # Sampling a task T_j from D_val
          val_rec_input = batch["input_ids"][j].unsqueeze(0).to(device)
          label = batch["label"][j].unsqueeze(0).to(device)
          reconstructed_sentence = reconstructor(input_ids=val_rec_input,labels=batch["labels"][j].unsqueeze(0).to(device))
          val_rec_input = val_rec_input.type(torch.FloatTensor).to(device)
          predicted_label = discriminator(val_rec_input)
          predicted_label.type(torch.LongTensor)
          style_loss = criterion(predicted_label, label)
          val_loss = float(style_loss) + float(reconstructed_sentence.loss)
          for name, param in reconstructor.state_dict().items():
              if not "weight" in name:
                continue
              param.copy_(param - beta * float(val_loss))
          val_progress_bar.update(1)
          val_losses.append(val_loss)
        # accelerator.backward(val_loss)
        optimizer.step()
        inner_training_progress_bar.update(1)
        val_losses_batch_wise[idx] = val_losses
      count+=1
      if count%5==0:
        save_model_to_hub(count)
      print(val_losses_batch_wise)
    total_training_progress_bar.update(1)

In [ ]:
start_training()

Total Training:   0%|          | 0/280 [00:00<?, ?it/s]

Inner Loop training (No.of.Batches):   0%|          | 0/282 [00:00<?, ?it/s]

Inner Loop training (No.of.examples in current batch):   0%|          | 0/64 [00:00<?, ?it/s]

Validation Examples in current batch:   0%|          | 0/64 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:32: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


...

Upload file pytorch_model.bin:   0%|          | 3.34k/850M [00:00<?, ?B/s]

To https://huggingface.co/buvnswrn/daml-t5-training
   f05b64d..d2d62fa  main -> main



{0: [11.251586139202118, 11.232080042362213, 11.053032636642456, 11.107726752758026, 11.130164980888367, 11.197354197502136, 11.056170642375946, 11.091613531112671, 10.953535974025726, 11.09688264131546, 10.951558351516724, 10.97103464603424, 10.933135330677032, 11.100903153419495, 11.018431425094604, 10.924140572547913, 11.127534031867981, 11.102787137031555, 11.150710582733154, 11.227204442024231, 11.113576292991638, 11.1619291305542, 11.105583667755127, 11.081246733665466, 11.088013470172882, 11.05470860004425, 10.909820914268494, 11.005417048931122, 11.01433527469635, 10.937950432300568, 11.005252957344055, 11.03497976064682, 11.029512524604797, 11.129327893257141, 11.231954574584961, 10.928163647651672, 11.241442024707794, 11.09340250492096, 11.035453379154205, 11.08215743303299, 11.081907570362091, 10.97161853313446, 11.238877952098846, 11.24441909790039, 11.216183423995972, 11.18902987241745, 11.080629348754883, 11.247099876403809, 10.913894176483154, 10.933850586414337, 11.0932

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:32: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


{0: [10.966684460639954, 10.957995474338531, 11.178650617599487, 11.205681502819061, 11.11045527458191, 11.130974650382996, 10.980133354663849, 11.054296910762787, 10.929636836051941, 11.173327207565308, 11.102648973464966, 11.101048469543457, 11.081611216068268, 11.022029101848602, 10.981489896774292, 11.058458924293518, 11.13511472940445, 10.965543031692505, 11.211080193519592, 10.92614370584488, 11.02752310037613, 11.074716746807098, 11.10909116268158, 11.225883960723877, 11.148376524448395, 11.197664856910706, 11.105987668037415, 11.130429446697235, 11.02755582332611, 11.203695178031921, 10.952188730239868, 10.951635122299194, 11.075889348983765, 11.267927587032318, 11.161791205406189, 11.027629911899567, 11.084629654884338, 11.142336368560791, 10.943905591964722, 11.158745050430298, 11.144166350364685, 11.116005778312683, 11.001322567462921, 11.043854832649231, 11.021689176559448, 11.137141644954681, 11.225260138511658, 10.964480638504028, 11.208209872245789, 11.042612969875336, 1

### Final Evaluation Procedure 

In [ ]:
overall_training_progress = tqdm(range(len(unseen_dataloader)),desc="Overall Progress")
innerloop_training_progress_bar = tqdm(range(BATCH_SIZE),desc="Inner Loop training (No.of.examples in current batch)")
for v_idx, data in enumerate(unseen_dataloader):
  innerloop_training_progress_bar.reset()
  for i in range(0,len(data["input_ids"])):
      input = data["input_ids"][i].unsqueeze(0).to(device)
      label = data["label"][i].unsqueeze(0).to(device)
      reconstructed_sentence = reconstructor(input_ids=input, labels=data["labels"][i].unsqueeze(0).to(device))
      input = input.type(torch.FloatTensor).to(device)
      predicted_label = discriminator(input)
      predicted_label.type(torch.LongTensor)
      style_loss = criterion(predicted_label, label)
      val_loss = float(style_loss) + float(reconstructed_sentence.loss)
      for name, param in reconstructor.state_dict().items():
          if not "weight" in name:
            continue
          param.copy_(param - beta * float(val_loss))
      innerloop_training_progress_bar.update(1)
  optimizer.step()
  overall_training_progress.update(1)

Overall Progress:   0%|          | 0/44 [00:00<?, ?it/s]

Inner Loop training (No.of.examples in current batch):   0%|          | 0/64 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:1806: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:32: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


### Test the model

In [ ]:
from transformers import pipeline

# Replace this with your own checkpoint
model_checkpoint = "daml-t5"
translator = pipeline("translation", model=model_checkpoint)
translator("Default to expanded threads")

/usr/local/lib/python3.7/dist-packages/transformers/pipelines/__init__.py:654: UserWarning: "translation" task was used, instead of "translation_XX_to_YY", defaulting to "translation_en_to_de"
  UserWarning,


[{'translation_text': ''}]

In [ ]:
translator(
    "Unable to import %1 using the OFX importer plugin. This file is not the correct format."
)

[{'translation_text': ''}]

### Installing Prerequisites

In [ ]:
!pip install sacrebleu

     |████████████████████████████████| 90 kB 4.9 MB/s 


### Computing Metrics

In [ ]:
from datasets import load_metric

metric = load_metric("sacrebleu")

In [ ]:
reconstructor.eval()
for batch in tqdm(eval_dataloader):
        with torch.no_grad():
            generated_tokens = accelerator.unwrap_model(reconstructor).generate(
                batch["input_ids"],
                attention_mask=batch["attention_mask"],
                max_length=128,
            )
        labels = batch["labels"]

        # Necessary to pad predictions and labels for being gathered
        generated_tokens = accelerator.pad_across_processes(
            generated_tokens, dim=1, pad_index=rec_tokenizer.pad_token_id
        )
        labels = accelerator.pad_across_processes(labels, dim=1, pad_index=-100)

        predictions_gathered = accelerator.gather(generated_tokens)
        labels_gathered = accelerator.gather(labels)

        decoded_preds, decoded_labels = postprocess(predictions_gathered, labels_gathered)
        # print(decoded_preds)
        # print(decoded_labels)
        # break
        metric.add_batch(predictions=decoded_preds, references=decoded_labels)

  0%|          | 0/44 [00:00<?, ?it/s]

In [ ]:
results = metric.compute()

In [ ]:
print(results)

{'score': 0.0, 'counts': [0, 0, 0, 0], 'totals': [0, 0, 0, 0], 'precisions': [0.0, 0.0, 0.0, 0.0], 'bp': 0.0, 'sys_len': 0, 'ref_len': 270667}
